In [5]:
import os
import gc
from tqdm import tqdm
import pandas as pd
import geopandas as gpd
from shapely.geometry import LineString
import matplotlib.pyplot as plt

In [26]:
import numpy as np

In [6]:
def get_ookla_nuts_level(nuts, read_root, folder, file, eu_range):
    # read ookla data, reproject and calculate the area of each tile
    print(read_root + r'/' + folder + r'/' + file)
    ookla_global = gpd.read_file(read_root + r'/' + folder + r'/' + file)
    ookla_global.to_crs('EPSG:3035', inplace = True)
    ookla_global['Shape_Area'] = ookla_global.area    
    
    # extract ookla polygon to centroids
    ookla_global.geometry = ookla_global['geometry'].centroid

    # musk the centroids by NUTS boundary
    ookla = gpd.clip(ookla_global, eu_range)
    del ookla_global
    gc.collect()

    # calculate the average download and upload data of all ookla points that fall within certain NUTS region
    speed_dict = {}
    unit = 'kbps'
    freq = 'quarter'
    for nuts_id in tqdm(nuts['NUTS_ID']):
        area = nuts[nuts['NUTS_ID']==nuts_id]
        ookla_within = gpd.sjoin(ookla, area, how='inner')
        if len(ookla_within)<1:
            avg_d_kpbs = 'NA'
            avg_u_kbps = 'NA'
        else:
            ookla_within['area*d'] = ookla_within['avg_d_kbps']*ookla_within['Shape_Area']
            ookla_within['area*u'] = ookla_within['avg_u_kbps']*ookla_within['Shape_Area']
            avg_d_kpbs = ookla_within['area*d'].sum()/ookla_within['Shape_Area'].sum()
            avg_u_kbps = ookla_within['area*u'].sum()/ookla_within['Shape_Area'].sum()
        speed_dict[nuts_id] = [quarter, network_type, unit, freq, avg_d_kpbs, avg_u_kbps, year]

    del ookla
    gc.collect()
    
    return speed_dict    

In [7]:
if __name__ == "__main__":
    nuts = gpd.read_file('/data/xiang/1-Data/NUTS/NUTS_RG_01M_2021_3035.shp')
    eu_range = gpd.read_file('/data/xiang/1-Data/NUTS/eu.shp')
    
    read_root = '/data/xiang/1-Data/Ookla'
    for folder in tqdm(os.listdir(read_root)[2:]): 
        for file in os.listdir(read_root + '//' + folder):
            if file.endswith('.shp'):
                # get the input variable from file paths
                year = folder.split('-')[0]
                quarter = int(folder.split('-')[1])//3+1
                network_type = folder.split('_')[-2]

                #  concatenante df from different quarters and years into one
                speed_dict = get_ookla_nuts_level(nuts, read_root, folder, file, eu_range)
                speed_df = pd.DataFrame(speed_dict).T
                speed_df.reset_index(inplace=True)
                speed_df.columns = ['geo', 'quarter', 'network_type', 'unit', 'freq', 'download', 'upload', 'obsTime']

                # reshape the df and save it
                reshap_df = pd.melt(speed_df, id_vars=['geo', 'quarter', 'unit', 'freq', 'obsTime','network_type'], value_vars = ['download', 'upload'], var_name = 'direction', value_name = 'obsValue')
                reshap_df.to_csv('/data/xiang/3-case studies/0-ookla data/separate quarters' + r'/' + folder + '.csv')

  0%|                                                    | 0/40 [00:00<?, ?it/s]

/data/xiang/1-Data/Ookla/2024-01-01_performance_mobile_tiles/gps_mobile_tiles.shp



  2%|▉                                      | 1/40 [21:32<14:00:05, 1292.44s/it]

/data/xiang/1-Data/Ookla/2019-04-01_performance_mobile_tiles/gps_mobile_tiles.shp



  5%|█▉                                     | 2/40 [54:41<17:58:07, 1702.31s/it]

...


 95%|██████████████████████████████████▏ | 38/40 [21:09:05<1:06:30, 1995.10s/it]

/data/xiang/1-Data/Ookla/2020-01-01_performance_mobile_tiles/gps_mobile_tiles.shp



 98%|█████████████████████████████████████ | 39/40 [21:31:15<29:55, 1795.65s/it]

/data/xiang/1-Data/Ookla/2022-01-01_performance_mobile_tiles/gps_mobile_tiles.shp



100%|██████████████████████████████████████| 40/40 [21:52:20<00:00, 1968.52s/it]


In [49]:
# concatenate all csv of separate quarters into a full csv and export it
quarter_path = '/data/xiang/3-case studies/0-ookla data/separate quarters'
df_concat = None
for quarter_file in os.listdir(quarter_path):
    if quarter_file.endswith('.csv'):
        df_temp = pd.read_csv(quarter_path + r'/' + quarter_file, index_col=0)
        df_concat = df_temp if df_concat is None else pd.concat([df_concat, df_temp])
        
df_concat.to_csv('/data/xiang/3-case studies/0-ookla data/ookla_nuts2021.csv', na_rep='NA')